# Nombres de Bell - l'explosion combinatoire

Marc Lorenzi

20 mai 2021

In [ ]:
import matplotlib.pyplot as plt
import math

**Remarque.** Dans ce qui suit, nous aurons quelquefois à estimer la complexité d'une fonction. Pour évaluer cette complexité, nous compterons le nombre d'opérations arithmétiques (addition, multiplication, ...) effectuées par la fonction. Nous nous contenterons d'estimations, sans entrer dans les micro-détails.

## 0. Fonctions basiques

La fonction `power_dn` prend en paramètres deux entiers naturels $x$ et $k$. Elle renvoie

$$x^{\underline k}=x(x-1)\ldots(x-k+1)$$

La complexité de cette fonction est $O(k)$.

In [ ]:
def power_dn(x, k):
    p = 1
    for i in range(k): p *= (x - i)
    return p

In [ ]:
print([power_dn(5, k) for k in range(10)])

Pour tout entier naturel $n$, on a

$$n!=n^{\underline n}$$

La complexité de la fonction `fact` ci-dessous est $O(n)$.

In [ ]:
def fact(n):
    return power_dn(n, n)

In [ ]:
print([fact(k) for k in range(10)])

Pour tout $n\in\mathbb N$, et tout $k\in[0,n]$,

$$\binom n k=\frac{n^{\underline k}}{k!}$$

La complexité de la fonction `binom` ci-dessous est $O(k)$.

In [ ]:
def binom(n, k):
    return power_dn(n, k) // fact(k)

In [ ]:
print([binom(6, k) for k in range(7)])

## 1. Partitions, première approche

Dans tout le notebook nous représenterons un ensemble (fini) en Python par la liste de ses éléments. Nous ne chercherons pas l'efficacité absolue (mais nous ne nous contenterons pas non plus d'écrire n'importe quoi !). L'idée sous-jacente à ce qui va suivre est la suivante :

Lorsqu'on cherche à dénombrer certaines quantités relatives à un ensemble $E$, on procède souvent de la façon suivante :

- Si $E=\emptyset$, c'est facile.
- Sinon, on se donne $a\in E$ et on pose $E'=E\setminus \{a\}$. On cherche ensuite à se ramener à un dénombrement relatif à $E'$.

### 1.1 Partitions d'un ensemble

Soit $E$ un ensemble. Une *partition* de $E$ est un ensemble $P$ de parties de $E$ vérifiant

- $(P_1)\quad \forall A\in P, A\ne \emptyset$
- $(P_2)\quad \forall A,B\in P, A\ne B\implies A\cap B=\emptyset$
- $(P_3)\quad \bigcup_{A\in P}A=E$

Nous noterons $\text{Part}(E)$ l'ensemble des partitions de $E$.

### 1.2. Créer toutes les partitions

Remarquons que 

$$\text{Part}(\emptyset)=\{\emptyset\}$$

car l'unique partition de $\emptyset$ est la partition vide $\emptyset$.

Soit maintenant $E$ un ensemble non vide. Soit $a\in E$. On a $E=E'\cup\{a\}$ où $|E'|=|E|-1$. Les partitions de $E$ sont obtenues de la façon suivante :

- On choisit la partie de la partition $P$ qui contient $a$. Cela revient à choisir une **partie** $A$ de $E'$.
- Pour chaque partition $P$ de la **différence** $E'\setminus A$, $P\cup \{A\cup\{a\}\}$ est une partition de $E$.
- Toutes les partitions de $E$ sont de cette forme.

Il nous suffit donc d'écrire 

- une fonction qui renvoie les **parties** d'un ensemble.
- une fonction qui renvoie la **différence** de deux ensembles.

Voici la fonction `parties`. Elle prend en paramètre un ensemble $E$ et renvoie l'ensemble des parties de $E$.

- Si $E=\emptyset$, $\mathcal P(E)=\{\emptyset\}$.
- Sinon, soit $a\in E$. Soit $E'=E\setminus \{a\}$. Les parties de $E$ sont alors

    - Les parties de $E'$.
    - Les ensembles $A\cup\{a\}$ où $A$ est une partie de $E'$. 

In [ ]:
def parties(E):
    if E == []: return [[]]
    else:
        a = E[-1]
        E1 = E[:-1]
        P1 = parties(E1)
        return P1 + [P + [a] for P in P1]

In [ ]:
parties([1, 2, 3])

Que vaut $\mathcal P(\mathcal P(\mathcal P(\mathcal P(\emptyset))))$ ? Jupyter refuse d'afficher le résultat. Alors écrivons la réponse dans un fichier.

In [ ]:
ps = parties(parties(parties(parties(parties([])))))
ps = str(ps)
n = len(ps)
print(n)
f = open('beurk.txt', 'w')
nblig = n // 80
for k in range(nblig):
    f.write(ps[80 * k: 80 * (k + 1)])
    f.write('\n')
f.write(ps[80 * nblig:-1])
f.close()

Le fichier en question fait $9$Mo. Un éditeur de texte finira par l'ouvrir, après quelques souffrances.

Et voici la fonction `difference`. Elle prend en paramètres deux ensembles $E$ et $F$ et renvoie l'ensemble $E\setminus F$. Cette fonction illustre bien la phrase « Nous ne chercherons pas l'efficacité absolue » : même si son code ne fait qu'une ligne, sa complexité est en $O(|E|\times |F|)$.

In [ ]:
def difference(E, F):
    return [x for x in E if x not in F]

In [ ]:
difference([1, 2, 3, 4, 5, 6], [1, 3, 5])

La fonction `partitions` est maintenant « immédiate ». Elle prend en paramètre un ensemble $E$. Elle renvoie l'ensemble des partitions de $E$, c'est à dire une liste de listes de listes.

In [ ]:
def partitions(E):
    if E == []: return [[]]
    else:
        a = E[-1]
        E1 = E[:-1]
        s = []
        for A in parties(E1):
            s1 = [P + [A + [a]] for P in partitions(difference(E1, A))]
            s = s + s1
        return s

In [ ]:
ps = partitions([1, 2, 3, 4, 5, 6])
print(len(ps))
print(ps)

### 1.3. Les nombres de Bell

Le $n$ième nombre de Bell est 

$$B_n=|\text{Part}(E)|$$

où $E$ est un ensemble de cardinal $n$. La fonction `partitions` permet évidemment de déterminer $B_n$ mais il est relativement absurde de **calculer toutes les partitions** pour savoir combien il y en a ! Soyons plus rusés.

On a évidemment $B_0=1$. Soit maintenant $E$ un ensemble de cardinal $n+1$, où $n\in\mathbb N$. Soit $a\in E$. Écrivons $E=E'\cup \{a\}$ où $E'$ est de cardinal $n$. De façon « informelle », comme nous l'avons déjà vu, une partition $P$ de $E$ est construite comme suit :

- On choisit $k\in [0,n]$.
- On choisit une partie $A$ de $E'$ de cardinal $k$ : il y a $\binom n k$ possibilités.
- On partitionne $E'\setminus A$ : il y a $B_{n-k}$ possibilités puisque cet ensemble est de cardinal $n-k$.

Ainsi,

$$B_{n+1}=\sum_{k=0}^n\binom n k B_{n-k}=\sum_{k=0}^n\binom n k B_{k}$$

La fonction `bell` prend un entier $N$ en paramètre. Elle renvoie la liste $[B_0,B_1,\ldots,B_N]$.

In [ ]:
def bell(N):
    bs = [1]
    for n in range(N):
        s = 0
        for k in range(n + 1):
            s += binom(n, k) * bs[k]
        bs.append(s)
    return bs

In [ ]:
print(bell(10))

Voici $B_{300}$.

In [ ]:
print(bell(300)[-1])

### 1.4 Complexité

Remarquons le petit temps d'attente. Notre fonction `bell` est assez inefficace. Notons $C_N$ la complexité du calcul de la liste $[B_0,\ldots,B_N]$. Sans donner trop de détails, estimons $C_N$ :

La boucle sur $k$ calcule les $n+1$ coefficients binomiaux $\binom n k$. Chacun de ces coefficients est calculé en temps $O(k)$ et, « donc », la boucle sur $k$ s'exécute en temps 

$$O\left(\sum_{k=0}^n k\right)=O(n^2)$$

Chaque itération sur $n$ prend donc un temps $O(n^2)$, et $n$ varie de 0 à $N$. « Ainsi », 

$$C_N=O\left(\sum_{n=0}^N n^2\right)= O(N^3)$$

Nous ferons mieux bientôt, en « descendant » à $O(N^2)$. Pour l'instant, il serait déraisonnable de calculer, par exemple, le millième nombre de Bell, puisque $1000^3= 1$ milliard.

## 1.5 Graphe

Les nombres de Bell deviennent vite très très gros. Voici, en coordonnées logarithmiques, le graphe de $B_n$ en fonction de $n$.

In [ ]:
plt.rcParams['figure.figsize'] = (12, 6)

In [ ]:
def plot_bell(n):
    bs = bell(n)
    plt.semilogy(range(n + 1), bs, 'k')
    plt.grid()

In [ ]:
plot_bell(100)

## 2. Partitions, une meilleure approche

### 2.1 Partitions de cardinal fixé

Pour tout ensemble $E$ et tout entier naturel $k$, notons $\text{Part}_k(E)$ l'ensemble des partitions de $E$ en $k$ sous-ensembles.

Soit $E$ un ensemble fini de cardinal $n$.

Si $E=\emptyset$, $\text{Part}_k(E)=\emptyset$ si $k\ne 0$ et $\{\emptyset\}$ si $k=0$.

Supposons $E\ne\emptyset$. 

- On a alors $\text{Part}_0(E)=\emptyset$. 
- Si $k\ge 1$, soit $a\in E$. Écrivons $E=E'\cup \{a\}$ où $E'$ est de cardinal $n-1$. Les partitions de $E$ de cardinal $k$ sont de deux types :

    - Celles où $\{a\}$ est l'un des éléments de la partition. Elles sont obtenues en prenant les partitions de $E'$ de cardinal $k-1$ et en rajoutant à ces partitions le singleton $\{a\}$.
    - Les autres. Elles sont obtenues en prenant les partitions de $E'$ de cardinal $k$ et en rajoutant $a$ à l'un des éléments de ces partitions.

In [ ]:
def partitions1(E, k):
    if E == []: 
        if k == 0: return [[]]
        else: return []
    elif k == 0: return []
    else:
        a = E[-1]
        E1 = E[:-1]
        ps1 = partitions1(E1, k - 1)
        qs1 = [P + [[a]] for P in ps1]
        ps2 = partitions1(E1, k)
        qs2 = []
        for P in ps2:
            qs2 = qs2 + ajouter(P, a)
        return qs1 + qs2

La fonction `ajouter` fait l'opération compliquée. Elle prend en paramètre une partition $P$ (de cardinal, disons, $k$) et un objet $a$. Elle renvoie le liste des $k$ partitions obtenues en rajoutant $a$ à l'un des éléments de $P$.

In [ ]:
def ajouter(P, a):
    s = []
    for X in P:
        P1 = []
        for Y in P:
            if Y == X: P1.append(Y + [a])
            else: P1.append(Y)
        s.append(P1)
    return s

In [ ]:
print(partitions1([1, 2, 3, 4, 5], 3))

### 2.2 Les nombres de Stirling

Pour tout ensemble fini $E$ de cardinal $n$ et tout $k\in\mathbb N$, notons

$${n\brace  k}=|\text{Part}_k(E)|$$

Les nombres $n \brace k$ sont les *nombres de Stirling* (de deuxième espèce). En reprenant la discussion du paragraphe précédent, il est facile d'obtenir des relations de récurrence.

- Si $n=0$, ${n\brace k}=1$ si $k=0$ et $0$ sinon.
- Si $n\ge 1$, soit $a\in E$. Écrivons $E=E'\cup \{a\}$ où $E'$ est de cardinal $n-1$. Les partitions de $E$ sont de deux types :

    - Celles où $\{a\}$ est un élément de la partition. Elles sont obtenues en prenant les partitions de $E'$ de cardinal $k-1$ et en rajoutant à ces partitions le singleton $\{a\}$. Il y en a ${n - 1 \brace k - 1}$.
    - Les autres. Elles sont obtenues en prenant les partitions de $E'$ de cardinal $k$ et en rajoutant $a$ à l'un des éléments de ces partitions. Pour chaque partition de $E'$ on peut donc créer $k$ telles partitions de $E$. Il y a donc au total $k{n - 1\brace k}$ telles partitions. Ainsi,
    
$${n\brace k} = {n - 1\brace k - 1} + k {n - 1\brace k}$$

La fonction `stirling` renvoie la matrice des $n\brace k$ pour $0\le n\le N$ et $0\le k\le N$.

In [ ]:
def stirling(N):
    s = (N + 1) * [None]
    for n in range(N + 1):
        s[n] = (N + 1) * [0]
    s[0][0] = 1
    for n in range(1, N + 1):
        for k in range(1, n + 1):
            s[n][k] = s[n - 1][k - 1] + k * s[n - 1][k]
    return s

In [ ]:
N = 10
st = stirling(N)
for n in range(N + 1):
    for k in range(N + 1):
        print('%6d' % st[n][k], end ='')
    print()

### 2.3 Retour aux nombres de Bell

On a bien entendu pour tout entier $n$,

$$B_n=\sum_{k=0}^n{n\brace k}$$

La fonction `bell1` reprend le code de la fonction `stirling`, mais utilise un espace en $O(N)$ au lieu de $O(N^2)$. Elle renvoie la liste $[B_0,\ldots, B_N]$.

In [ ]:
def bell1(N):
    bs = (N + 1) * [None]
    s = (N + 1) * [0]
    s[0] = 1
    bs[0] = 1
    for n in range(1, N + 1):
        s1 = (N + 1) * [0]
        for k in range(1, n + 1):
            s1[k] = s[k - 1] + k * s[k]
        s = s1
        bs[n] = sum(s)
    return bs

In [ ]:
bell1(10)

La fonction `bell1` est beaucoup plus efficace que la fonction `bell` que nous avions écrite au début du notebook. Clairement, sa complexité est en $O(N^2)$ puisque nous avons deux boucles imbriquées sur $n$ et $k$. Bien entendu, les opérations arithmétiques se font sur de très grands entiers, et une étude plus poussée de la complexité devrait prendre en compte les tailles de ces entiers.

Voici le 1000ème nombre de Bell.

In [ ]:
bell1(1000)[-1]

## 3. Annexe - La taille des nombres de Bell

Les nombres de Bell $B_n$ deviennent très vite grands lorsque $n$ augmente. Très grands comment ?

Il est possible de donner des estimations de $B_n$. En voici, sans démonstration.

### 3.1 Développement asymptotique 

Le développement asymptotique ci-dessous est dû à De Bruijn (1958).

$$\frac{\ln B_n}n=\ln n-\ln\ln n-1+\frac{\ln\ln n}{\ln n}+\frac 1 {\ln n}+\frac 1 2\left(\frac{\ln\ln n}{\ln n}\right)^2+O\left(\frac{\ln\ln n}{\ln n}\right)^2$$

On peut en déduire que pour tout $\varepsilon>0$ et tout entier $n$ assez grand,

$$\left(\frac{n}{e\ln n}\right)^n<B_n<\left(\frac{n}{e^{1-\varepsilon}\ln n}\right)^n$$

La fonction `bornes` renvoie le minorant et le majorant de l'inégalité ci-dessus. Elle est l'exemple ultime d'une fonction qui ne sert à rien.

In [ ]:
def bornes(n, eps):
    if n <= 1: return (1, 1)
    x = (n / (math.e * math.log(n))) ** n
    y = (n / (math.e ** (1 - eps) * math.log(n))) ** n
    return (x, y)

In [ ]:
bornes(200, 1e-1)

Le problème de ces inégalités est qu'elles ne sont vraies que pour $n$ voisin de l'infini.

En clair, on ne sait pas si les valeurs renvoyées par `bornes` encadrent $B_n$ : Pour tous $n,\varepsilon$, la valeur renvoyée est correcte ... ou pas.  Par exemple, il n'est pas certain que $B_{200}$ soit bien entre les deux réels que nous venons de calculer. D'ailleurs, il n'y est pas 😀.

In [ ]:
math.log(bell1(200)[-1], 10)

Voici, en noir, les nombres de Bell, et en rouge les bornes censées encadrer ceux-ci. Selon les valeur de `eps`, la courbe noire est entre les courbes rouges ... ou pas.

In [ ]:
def tracer_bell_mino_majo(n, eps):
    xs = range(n + 1)
    ys = bell1(n)
    bs = [bornes(x, eps) for x in xs]
    zs = [z[0] for z in bs]
    ts = [z[1] for z in bs]
    plt.semilogy(xs, ys, 'k')
    plt.semilogy(xs, zs, 'r')
    plt.semilogy(xs, ts, 'r')
    plt.grid()

In [ ]:
tracer_bell_mino_majo(100, 0.5)

### 3.2 Un majorant effectif

Voici un majorant **effectif** de $B_n$, c'est à dire un majorant vrai pour tout entier $n$. Ce résultat est dû à D. Berend et T. Tassa (2010).

Pour tout entier $n\ge 1$,

$$B_n<\left(\frac{0.792 n}{\ln (n + 1)}\right)^n$$

In [ ]:
def majorant(n):
    if n == 0: return 1
    else:
        x = (0.792 * n / math.log(n + 1)) ** n
        return x

In [ ]:
majorant(200)

In [ ]:
math.log(bell1(200)[-1], 10)

Voici, en noir, les nombres de Bell, et en rouge le majorant de Berend et Tassa.

In [ ]:
def tracer_bell_majo(n):
    xs = range(n + 1)
    ys = bell1(n)
    zs = [majorant(x) for x in xs]
    plt.semilogy(xs, ys, 'k')
    plt.semilogy(xs, zs, 'r')
    plt.grid()

In [ ]:
tracer_bell_majo(100)

*Bibliographie.*

- D. Berend, T. Tassa, Improved Bounds on Bell Numbers and on Moments of Sums of Random Variables - Journal of Probability and Mathematical Statistics Vol. 30, Fasc. 2 (2010), pp. 185-205.